<a href="https://colab.research.google.com/github/hatkaran/Amex-Project/blob/main/Amex_Training_%26_Prediction.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
import pandas as pd

In [ ]:
from google.colab import drive
drive.mount("/content/drive")

Mounted at /content/drive


In [ ]:
train = pd.read_csv(r"/content/drive/MyDrive/Req. Amex Docs/train.csv")

In [ ]:
Eval = pd.read_csv(r"/content/drive/MyDrive/Req. Amex Docs/Eval.csv")

### Feature Selection

In [ ]:
!pip install catboost

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 98.6/98.6 MB 8.8 MB/s eta 0:00:00


In [ ]:
from sklearn.feature_selection import RFECV
from sklearn.model_selection import StratifiedKFold, train_test_split
from lightgbm import LGBMClassifier
from imblearn.combine import SMOTETomek
from catboost import CatBoostClassifier

# Select the features
X = train.drop(['ind_recommended', 'activation', 'customer', 'merchant'], axis=1)

# Select the target variables
Y = train['ind_recommended']

# Split data into train and test sets with stratified sampling
X_tr, X_test_y, Y_tr, Y_test_y = train_test_split(X, Y, test_size=0.20, random_state=42, stratify=Y)

# Initialize the classifier for feature selection (replace RandomForestClassifier with LGBMClassifier)
estimator_Y = LGBMClassifier()

# Initialize the RFE selectors with cross-validation for each target variable
rfecv_Y = RFECV(estimator=estimator_Y, cv=StratifiedKFold(), scoring='accuracy')

# Fit the RFE selectors on the training data for each target variable
rfecv_Y.fit(X_tr, Y_tr)

# Combine the selected features based on some criteria
selected_features_Y = X_tr.columns[rfecv_Y.support_].tolist()

# Print the selected feature names
print("Selected features for ind_recommended: ", selected_features_Y)


[LightGBM] [Info] Number of positive: 11153, number of negative: 76542
[LightGBM] [Warning] Auto-choosing col-wise multi-threading, the overhead of testing was 0.029822 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 9088
[LightGBM] [Info] Number of data points in the train set: 87695, number of used features: 88
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.127179 -> initscore=-1.926131
[LightGBM] [Info] Start training from score -1.926131
[LightGBM] [Info] Number of positive: 11153, number of negative: 76542
[LightGBM] [Warning] Auto-choosing col-wise multi-threading, the overhead of testing was 0.028516 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 9086
[LightGBM] [Info] Number of data points in the train set: 87695, number of used features: 87
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.127179 -> initscore=-1.926131
[LightGBM] [Info] Start training from score -1.926131
[Light

In [ ]:
from sklearn.feature_selection import RFECV
from sklearn.model_selection import StratifiedKFold, train_test_split
from lightgbm import LGBMClassifier
from imblearn.combine import SMOTETomek
from catboost import CatBoostClassifier

# Select the features
X = train.drop(['ind_recommended', 'activation', 'customer', 'merchant'], axis=1)

# Select the target variables
Z = train['activation']

# Split data into train and test sets with stratified sampling
X_tr, X_test_z, Z_tr, Z_test_z = train_test_split(X, Z, test_size=0.20, random_state=42, stratify=Z)

# Initialize the classifier for feature selection (replace RandomForestClassifier with LGBMClassifier)
estimator_Z = LGBMClassifier()

# Initialize the RFE selectors with cross-validation for each target variable
rfecv_Z = RFECV(estimator=estimator_Z, cv=StratifiedKFold(), scoring='accuracy')

# Fit the RFE selectors on the training data for each target variable
rfecv_Z.fit(X_tr, Z_tr)

# Combine the selected features based on some criteria
selected_features_Z = X_tr.columns[rfecv_Z.support_].tolist()

# Print the selected feature names
print("Selected features for activation: ", selected_features_Z)


[LightGBM] [Info] Number of positive: 26382, number of negative: 61313
[LightGBM] [Warning] Auto-choosing row-wise multi-threading, the overhead of testing was 0.009714 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 9099
[LightGBM] [Info] Number of data points in the train set: 87695, number of used features: 88
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.300838 -> initscore=-0.843310
[LightGBM] [Info] Start training from score -0.843310
[LightGBM] [Info] Number of positive: 26382, number of negative: 61313
[LightGBM] [Warning] Auto-choosing row-wise multi-threading, the overhead of testing was 0.009763 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 9097
[LightGBM] [Info] Number of data points in the train set: 87695, number of used features: 87
[LightGBM] [

### Rebalancing Data

In [ ]:
# Separate the target variable and features
X_trainu = train[selected_features_Y]
Y_trainu = train["ind_recommended"]

# Apply SMOTETomek to each target variable separately
smt_Y = SMOTETomek(random_state=42)

X_train, Y_train = smt_Y.fit_resample(X_trainu, Y_trainu)

#------------------------------------------------

In [ ]:
# Separate the target variable and features
trainu_X = train[selected_features_Z]
trainu_Z = train["activation"]

# Apply SMOTETomek to each target variable separately
smt_Z = SMOTETomek(random_state=42)

train_X, train_Z = smt_Z.fit_resample(trainu_X, trainu_Z)


### Installing Catboost

In [ ]:
!pip install catboost

### Catboost

In [ ]:
# Initialize the CatBoost classifier
catboost_Y = CatBoostClassifier()

# Train the model
catboost_Y.fit(X_train, Y_train)

# Make predictions on the test set
Y_pred_test_rec = catboost_Y.predict(X_test_y)


# Create a DataFrame with the predictions
Y_pred = pd.DataFrame(Y_pred_test_rec, columns=["ind_recommended"])
#------------------------------------------------

Learning rate set to 0.106112
0:	learn: 0.6660131	total: 98.8ms	remaining: 1m 38s
1:	learn: 0.6329865	total: 154ms	remaining: 1m 16s
2:	learn: 0.6129722	total: 201ms	remaining: 1m 6s
3:	learn: 0.5976994	total: 253ms	remaining: 1m 2s
4:	learn: 0.5666154	total: 308ms	remaining: 1m 1s
5:	learn: 0.5558409	total: 355ms	remaining: 58.9s
6:	learn: 0.5471628	total: 415ms	remaining: 58.8s
7:	learn: 0.5390124	total: 503ms	remaining: 1m 2s
8:	learn: 0.5299038	total: 571ms	remaining: 1m 2s
9:	learn: 0.5223904	total: 676ms	remaining: 1m 6s
10:	learn: 0.5147683	total: 766ms	remaining: 1m 8s
11:	learn: 0.5092949	total: 813ms	remaining: 1m 6s
12:	learn: 0.4981871	total: 861ms	remaining: 1m 5s
13:	learn: 0.4702875	total: 920ms	remaining: 1m 4s
14:	learn: 0.4457726	total: 990ms	remaining: 1m 4s
15:	learn: 0.4421969	total: 1.04s	remaining: 1m 3s
16:	learn: 0.4384094	total: 1.09s	remaining: 1m 3s
17:	learn: 0.4341161	total: 1.14s	remaining: 1m 2s
18:	learn: 0.4314249	total: 1.19s	remaining: 1m 1s
19:	lear

In [ ]:
# Initialize the CatBoost classifier
catboost_Z = CatBoostClassifier()

# Train the model
catboost_Z.fit(train_X, train_Z)

# Make predictions on the test set
Z_pred_test_act = catboost_Z.predict(X_test_z)

# Create a DataFrame with the predictions
Z_pred = pd.DataFrame(Z_pred_test_act, columns=["activation"])
#------------------------------------------------

Learning rate set to 0.089504
0:	learn: 0.6931534	total: 17.3ms	remaining: 17.3s
1:	learn: 0.6931487	total: 32.7ms	remaining: 16.3s
2:	learn: 0.6931724	total: 48.5ms	remaining: 16.1s
3:	learn: 0.6931624	total: 64.7ms	remaining: 16.1s
4:	learn: 0.6931413	total: 80.9ms	remaining: 16.1s
5:	learn: 0.6931009	total: 97.3ms	remaining: 16.1s
6:	learn: 0.6931010	total: 114ms	remaining: 16.2s
7:	learn: 0.6930403	total: 130ms	remaining: 16.1s
8:	learn: 0.6930281	total: 146ms	remaining: 16.1s
9:	learn: 0.6930513	total: 163ms	remaining: 16.1s
10:	learn: 0.6930587	total: 178ms	remaining: 16s
11:	learn: 0.6930319	total: 201ms	remaining: 16.6s
12:	learn: 0.6930064	total: 217ms	remaining: 16.5s
13:	learn: 0.6929961	total: 233ms	remaining: 16.4s
14:	learn: 0.6929693	total: 249ms	remaining: 16.4s
15:	learn: 0.6929635	total: 266ms	remaining: 16.3s
16:	learn: 0.6929730	total: 281ms	remaining: 16.2s
17:	learn: 0.6929452	total: 296ms	remaining: 16.2s
18:	learn: 0.6929375	total: 312ms	remaining: 16.1s
19:	lea

### Accuracy check of model

In [ ]:
from sklearn.metrics import confusion_matrix

# Calculate the confusion matrix
Y_confusion_matrix_rec = confusion_matrix(Y_test_y, Y_pred)
Z_confusion_matrix_act = confusion_matrix(Z_test_z, Z_pred)

# Unpack the confusion matrix values
Y_tn, Y_fp, Y_fn, Y_tp = Y_confusion_matrix_rec.ravel()
Z_tn, Z_fp, Z_fn, Z_tp = Z_confusion_matrix_act.ravel()

# Print the values
print("True Negative of Y (TN):", Y_tn)
print("True Negative of Z (TN):", Z_tn)

print("False Positive of Y (FP):", Y_fp)
print("False Positive of Z (FP):", Z_fp)


print("False Negative of Y (FN):", Y_fn)
print("False Negative of Z (FN):", Z_fn)


print("True Positive of Y (TP):", Y_tp)
print("True Positive of Z (TP):", Z_tp)



Y_accuracy = (Y_tp + Y_tn) / (Y_tp + Y_tn + Y_fp + Y_fn)
Z_accuracy = (Z_tp + Z_tn) / (Z_tp + Z_tn + Z_fp + Z_fn)

print("Y_accuracy : " , Y_accuracy)
print("Z_accuracy : " , Z_accuracy)

True Negative of Y (TN): 23747
True Negative of Z (TN): 9893
False Positive of Y (FP): 173
False Positive of Z (FP): 9268
False Negative of Y (FN): 2976
False Negative of Z (FN): 3929
True Positive of Y (TP): 509
True Positive of Z (TP): 4315
Y_accuracy :  0.8850939609560299
Z_accuracy :  0.5184455391351943


### Catboost on Evaluation Data

In [ ]:
# Initialize the CatBoost classifier
catboost = CatBoostClassifier()

# Train the model
catboost.fit(X_train, Y_train)

# Make predictions on the test set
X_eval = Eval.drop(["customer","merchant"],axis=1)
Y_pred_eval = catboost.predict(X_eval)

# Create a DataFrame with the predictions
Eval["activation"] = pd.DataFrame(Y_pred_eval, columns=["activation"])

Eval["activation"]

Learning rate set to 0.106112
0:	learn: 0.6660131	total: 56ms	remaining: 56s
1:	learn: 0.6329865	total: 110ms	remaining: 54.7s
2:	learn: 0.6129722	total: 153ms	remaining: 51s
3:	learn: 0.5976994	total: 208ms	remaining: 51.9s
4:	learn: 0.5666154	total: 262ms	remaining: 52.2s
5:	learn: 0.5558409	total: 318ms	remaining: 52.7s
6:	learn: 0.5471628	total: 373ms	remaining: 52.8s
7:	learn: 0.5390124	total: 426ms	remaining: 52.8s
8:	learn: 0.5299038	total: 475ms	remaining: 52.3s
9:	learn: 0.5223904	total: 531ms	remaining: 52.6s
10:	learn: 0.5147683	total: 578ms	remaining: 52s
11:	learn: 0.5092949	total: 627ms	remaining: 51.7s
12:	learn: 0.4981871	total: 675ms	remaining: 51.3s
13:	learn: 0.4702875	total: 731ms	remaining: 51.5s
14:	learn: 0.4457726	total: 801ms	remaining: 52.6s
15:	learn: 0.4421969	total: 852ms	remaining: 52.4s
16:	learn: 0.4384094	total: 906ms	remaining: 52.4s
17:	learn: 0.4341161	total: 951ms	remaining: 51.9s
18:	learn: 0.4314249	total: 1s	remaining: 51.7s
19:	learn: 0.4286332	

0         0.0
1         0.0
2         0.0
3         0.0
4         0.0
         ... 
116688    0.0
116689    0.0
116690    0.0
116691    1.0
116692    0.0
Name: activation, Length: 116693, dtype: float64

In [ ]:
from catboost import CatBoostRegressor

# Initialize the CatBoost classifier
regressor = CatBoostRegressor()

# Train the model
regressor.fit(X_train, Y_train)

# Make predictions on the test set
X_eval = Eval.drop(["customer","merchant"],axis=1)
Y_pred_eval = regressor.predict(X_eval)

# Create a DataFrame with the predictions
Eval["predicted_score"] = pd.DataFrame(Y_pred_eval, columns=["ind_recommended"])

Eval["predicted_score"]

Learning rate set to 0.09704
0:	learn: 0.4893915	total: 44.6ms	remaining: 44.6s
1:	learn: 0.4791252	total: 83.7ms	remaining: 41.8s
2:	learn: 0.4708942	total: 120ms	remaining: 39.7s
3:	learn: 0.4625952	total: 164ms	remaining: 40.9s
4:	learn: 0.4561188	total: 204ms	remaining: 40.7s
5:	learn: 0.4497958	total: 260ms	remaining: 43.1s
6:	learn: 0.4447309	total: 301ms	remaining: 42.7s
7:	learn: 0.4387922	total: 339ms	remaining: 42s
8:	learn: 0.4341777	total: 375ms	remaining: 41.3s
9:	learn: 0.4304931	total: 413ms	remaining: 40.9s
10:	learn: 0.4261548	total: 461ms	remaining: 41.4s
11:	learn: 0.4230673	total: 499ms	remaining: 41s
12:	learn: 0.4203021	total: 534ms	remaining: 40.5s
13:	learn: 0.4174585	total: 575ms	remaining: 40.5s
14:	learn: 0.4146620	total: 611ms	remaining: 40.1s
15:	learn: 0.4118640	total: 650ms	remaining: 40s
16:	learn: 0.4088800	total: 691ms	remaining: 39.9s
17:	learn: 0.4068876	total: 724ms	remaining: 39.5s
18:	learn: 0.4042881	total: 762ms	remaining: 39.4s
19:	learn: 0.402

0         0.241869
1         0.349685
2         0.197530
3         0.194673
4         0.538303
            ...   
116688    0.468320
116689    0.289797
116690    0.192130
116691    0.554756
116692    0.229660
Name: predicted_score, Length: 116693, dtype: float64

In [ ]:
Eval = Eval[Eval["activation"]==1][["customer","merchant","predicted_score"]]

In [ ]:
Eval.head(50)

customer   merchant  predicted_score
5    467915.0   916733.0         0.679026
9    467915.0   623047.0         0.492306
18   467915.0   743677.0         0.679654
47   467915.0  1015143.0         0.579601
54   467915.0   706183.0         0.459153
290  467918.0   665136.0         0.383285
292  467918.0   676130.0         0.452574
293  467918.0   694489.0         0.534662
294  467918.0   877943.0         0.410395
296  467918.0   934166.0         0.520464
297  467918.0  1043052.0         0.393876
299  467918.0   623856.0         0.448496
300  467918.0   644196.0         0.426257
301  467918.0   684436.0         0.466788
303  467918.0   767428.0         0.450322
304  467918.0   788641.0         0.391012
305  467918.0  1027350.0         0.435134
306  467918.0   892529.0         0.449386
308  467918.0  1060511.0         0.410468
309  467918.0   639650.0         0.457907
310  467918.0   646427.0         0.493230
311  467918.0   650380.0         0.494966
312  467918.0   695820.0         0.650440
314  467918.0   917352.0         0.398925
315  467918.0  1000402.0         0.399157
316  467918.0  1015277.0         0.629198
317  467918.0   604802.0         0.402644
318  467918.0   708970.0         0.533833
319  467918.0   955865.0         0.393318
320  467918.0  1057139.0         0.670622
321  467918.0   629964.0         0.424810
322  467918.0   748674.0         0.437295
323  467918.0   946942.0         0.411019
324  467918.0   996063.0         0.419242
325  467918.0  1030065.0         0.347365
326  467918.0   712674.0         0.387408
328  467918.0   881651.0         0.470161
329  467918.0   675481.0         0.450224
331  467918.0   875762.0         0.494047
332  467918.0   909395.0         0.287832
333  467918.0   935286.0         0.377861
334  467918.0   939602.0         0.424740
335  467918.0   995704.0         0.502450
336  467918.0  1037520.0         0.439944
337  467918.0  1069417.0         0.648296
338  467918.0   949417.0         0.482863
340  467918.0   877620.0         0.510163
341  467918.0   900898.0         0.323303
342  467918.0   923535.0         0.459342
343  467918.0   968555.0         0.382586

In [ ]:
aa = Eval.groupby(["customer","merchant"])["predicted_score"].nlargest(10,keep='all').reset_index()
aa.head()

customer  merchant  level_2  predicted_score
0  462634.0  637734.0    49928         0.554008
1  462634.0  640917.0    49929         0.392370
2  462634.0  688775.0    49922         0.375800
3  462634.0  712665.0    49917         0.503438
4  462634.0  851170.0    49897         0.644818

In [ ]:
aa = aa[["customer","merchant","predicted_score"]]

In [ ]:
pd.set_option("display.max_rows",None)

aa

customer   merchant  predicted_score
0      462634.0   637734.0         0.554008
1      462634.0   640917.0         0.392370
2      462634.0   688775.0         0.375800
3      462634.0   712665.0         0.503438
4      462634.0   851170.0         0.644818
5      462634.0   894299.0         0.540002
6      462634.0   943844.0         0.619955
7      462634.0   974658.0         0.464429
8      462634.0   984007.0         0.420211
9      462634.0  1030117.0         0.523719
10     462635.0   734455.0         0.670845
11     462636.0   608458.0         0.489567
12     462636.0   613421.0         0.527187
13     462636.0   615918.0         0.501294
14     462636.0   621974.0         0.542413
15     462636.0   623889.0         0.480255
16     462636.0   629313.0         0.603704
17     462636.0   643257.0         0.480943
18     462636.0   643712.0         0.598416
19     462636.0   643827.0         0.583975
20     462636.0   651216.0         0.482824
21     462636.0   659542.0         0.518838
22     462636.0   666229.0         0.592688
23     462636.0   671834.0         0.466610
24     462636.0   678510.0         0.449094
25     462636.0   692772.0         0.536410
26     462636.0   702571.0         0.378469
27     462636.0   727258.0         0.508596
28     462636.0   733465.0         0.608706
29     462636.0   740030.0         0.449305
30     462636.0   755184.0         0.674847
31     462636.0   767189.0         0.402563
32     462636.0   785149.0         0.585057
33     462636.0   795958.0         0.682527
34     462636.0   798520.0         0.385161
35     462636.0   799412.0         0.447834
36     462636.0   821537.0         0.526445
37     462636.0   826706.0         0.458430
38     462636.0   832650.0         0.556430
39     462636.0   833851.0         0.553294
40     462636.0   834347.0         0.547881
41     462636.0   842839.0         0.678262
42     462636.0   852918.0         0.525158
43     462636.0   859960.0         0.441279
44     462636.0   861332.0         0.564371
45     462636.0   861363.0         0.644805
46     462636.0   862109.0         0.577604
47     462636.0   866974.0         0.489456
48     462636.0   884867.0         0.632995
49     462636.0   898500.0         0.583578
50     462636.0   906101.0         0.502310
51     462636.0   912088.0         0.521306
52     462636.0   921360.0         0.532928
53     462636.0   931672.0         0.639845
54     462636.0   945424.0         0.587418
55     462636.0   946091.0         0.534147
56     462636.0   948883.0         0.415067
57     462636.0   950441.0         0.579148
58     462636.0   975051.0         0.664047
59     462636.0   994518.0         0.578757
60     462636.0  1000015.0         0.609723
61     462636.0  1016427.0         0.584858
62     462636.0  1021149.0         0.565839
63     462636.0  1028803.0         0.597341
64     462636.0  1032818.0         0.582218
65     462636.0  1035418.0         0.492914
66     462636.0  1037050.0         0.454558
67     462636.0  1042826.0         0.438336
68     462636.0  1043245.0         0.611170
69     462636.0  1044790.0         0.629638
70     462636.0  1046758.0         0.517913
71     462636.0  1062712.0         0.590614
72     462636.0  1062831.0         0.512947
73     462636.0  1074832.0         0.587580
74     462637.0   708390.0         0.543228
75     462637.0  1049148.0         0.526295
76     462638.0   640992.0         0.567519
77     462638.0   738153.0         0.625259
78     462638.0   738842.0         0.576872
79     462638.0   856542.0         0.686466
80     462638.0   872268.0         0.657258
81     462638.0   878376.0         0.607793
82     462638.0   894891.0         0.512277
83     462638.0   898533.0         0.556475
84     462638.0   986098.0         0.609453
85     462638.0  1005907.0         0.574307
86     462638.0  1007298.0         0.611410
87     462638.0  1060607.0         0.505352
88     462638.0  1062040.0         0.601756
89     462639.0   599846.0         0.425080
90 